In [ ]:
import os
import configparser

import pandas as pd
import geopandas as gpd

from shapely.geometry import Point, Polygon, LineString, MultiLineString
from shapely import line_merge, shortest_line, line_locate_point, normalize, distance, difference
from shapely.affinity import scale, rotate,translate

import requests
import json
import osmnx as ox

import numpy as np
import matplotlib.pyplot as plt
from matplotlib.patches import Circle
from matplotlib.collections import LineCollection
from PIL import Image, ImageOps, ImageDraw

In [ ]:
#set filepaths
project_root = os.path.abspath(os.getcwd())
root = os.path.abspath(os.path.join(os.getcwd(), ".."))
config_file =  os.path.join(root, "config.cfg")

# geodata for shapefiles
config = configparser.ConfigParser()
config.read(config_file)
gdata_root = config["geodata"]["path"]

In [ ]:
#get the tram line from the Overpass AP

overpass_url = "http://overpass-api.de/api/interpreter"
overpass_query = """
[out:json];
area["name"="Berlin"]->.searchArea;
(
  node["route"="tram"]["ref"="M8"](area.searchArea);
  way["route"="tram"]["ref"="M8"](area.searchArea);
  relation["route"="tram"]["ref"="M8"](area.searchArea);
);
(._;>;);
out body;
"""
response = requests.get(overpass_url, params={'data': overpass_query})
data = response.json()

#save for later...
filename = os.path.join(gdata_root,'Berlin', 'Tram_route_M8.json')
with open(filename, "w") as json_file:
    json.dump(data, json_file, indent=4)

In [ ]:
#parse the nodes first 
unique_tags = set()
nodes = [element for element in data['elements'] if element['type'] == 'node']
for node in nodes:
    if 'tags' in node:
        unique_tags.update(node['tags'].keys())

unique_tags_list = list(unique_tags)

data_dict = {"id":[], "lat":[], "lon":[]} | {tag: [] for tag in unique_tags_list}

# Populate the data dictionary with values from JSON data
for node in nodes:
    data_dict["id"].append(node["id"])
    data_dict["lat"].append(node["lat"])
    data_dict["lon"].append(node["lon"])
    node_tags = node.get('tags', {})
    for tag in unique_tags_list:
        data_dict[tag].append(node_tags.get(tag, None))

df = pd.DataFrame(data_dict)
# convert into geodataframe
geometry = [Point(xy) for xy in zip(df['lon'].astype(float), df['lat'].astype(float))]
nodes_gdf = gpd.GeoDataFrame(df, crs="EPSG:4326", geometry = geometry).drop(columns=['lat','lon'])

In [ ]:
#now the ways
unique_tags = set()
nodes = {element['id']: (element['lon'], element['lat']) for element in data['elements'] if element['type'] == 'node'}
ways = [element for element in data['elements'] if element['type'] == 'way']
for way in ways:
    if 'tags' in way:
        unique_tags.update(way['tags'].keys())

unique_tags_list = list(unique_tags)
data_dict = {"id":[], "line":[]} | {tag: [] for tag in unique_tags_list}

for way in ways:
    data_dict["id"].append(way["id"])
    coords = [nodes[node_id] for node_id in way['nodes'] if node_id in nodes]
    if coords:
        data_dict["line"].append(LineString(coords))
    else:
        data_dict["line"].append(None)
    way_tags = way.get('tags', {})
    for tag in unique_tags_list:
        data_dict[tag].append(way_tags.get(tag, None))

df = pd.DataFrame(data_dict)

ways_gdf = gpd.GeoDataFrame(df, crs="EPSG:4326", geometry = "line")

In [ ]:
#and finally build relations from the ways.
#something tells me it should be a function... 
unique_tags = set()
relations = [element for element in data['elements'] if element['type'] == 'relation']
for relation in relations:
    if 'tags' in relation:
        unique_tags.update(relation['tags'].keys())

unique_tags_list = list(unique_tags)
data_dict = {"id":[], "geometry":[], "way_ids":[]} | {tag: [] for tag in unique_tags_list}

for relation in relations:
    data_dict["id"].append(relation["id"])
    way_ids = [element['ref'] for element in relation['members'] if (element['type'] == 'way' and element['role']=='')] # only non-platform and non-stop ways
    if way_ids:
        data_dict["geometry"].append(ways_gdf[ways_gdf.id.isin(way_ids)].geometry.union_all())
        data_dict["way_ids"].append(way_ids)
    else:
        data_dict["geometry"].append(None)
        data_dict["way_ids"].append(None)
    relation_tags = relation.get('tags', {})
    for tag in unique_tags_list:
        data_dict[tag].append(relation_tags.get(tag, None))

df = pd.DataFrame(data_dict)

relations_gdf = gpd.GeoDataFrame(df, crs="EPSG:4326", geometry='geometry')
#merge multilinestrings
# relations_gdf.geometry = relations_gdf.geometry.line_merge()

In [ ]:
#calculate lengths of the routes
relations_gdf['length']=relations_gdf.to_crs(epsg=25833).geometry.length
relations_gdf['length']

In [ ]:
#and take the longer ones
tram_routes=relations_gdf.iloc[[0,1]]
tram_routes

In [ ]:
nodes_gdf.to_file(os.path.join(gdata_root,'Berlin', 'tram_route_M8.gpkg'), driver='GPKG', layer='nodes')
ways_gdf.to_file(os.path.join(gdata_root,'Berlin', 'tram_route_M8.gpkg'), driver='GPKG', layer='ways')
relations_gdf.to_file(os.path.join(gdata_root,'Berlin', 'tram_route_M8.gpkg'), driver='GPKG', layer='relations')
tram_routes.to_file(os.path.join(gdata_root,'Berlin', 'tram_route_M8.gpkg'), driver='GPKG', layer='routes')

Collect building polygons along the route.

In [ ]:
#I do not want to fetch a lot of data in a huge bbox around the whole route, so the buildings a collected along each segment of the route
#at this point I realised that insted of manually parsing overpass output, I could have used onsmnx :D

#NB: it could be more effective to to use single sided buffers - that whould eliminate overlaps between buffered poligons and duplicated buildings in the resulting df,
#but could cause more headache, so it is easier to filter out duplicates later


# buffer 400 m aroud the way and get the bbox som oxmnx
def get_expanded_bbox(way_id):
    minx, miny, maxx, maxy=ways_gdf[ways_gdf.id == way_id].to_crs(epsg=25833).geometry.buffer(400).to_crs(epsg=4326).bounds.to_numpy().flatten().tolist()
    #note the N S E W placement required for osmnx 
    bbox = (maxy, miny, maxx, minx)
    return bbox

def get_buildings_from_around_way(way_id):
    bbox = get_expanded_bbox(way_id)
    return ox.features.features_from_bbox(bbox=bbox,tags = {'building': True})

In [ ]:
#cursed loops: iterate through way_id and collect buildings
frames= [get_buildings_from_around_way(id) for id_list in tram_routes.way_ids for id in id_list]

In [ ]:
buildings = pd.concat(frames)
buildings.head()
buildings=buildings.reset_index()
# buildings.duplicated() would not work directly, as there are node lists inside
print(sum(buildings['osmid'].duplicated()))
print(len(buildings['osmid'].unique()))

In [ ]:
#as expected, I've fetched some buildings multiple times - I recon it is still better compared to a huge bbox around the whole route
#select only unique polygons, drop na
buildings = buildings.loc[buildings['osmid'].drop_duplicates().index]

In [ ]:
buildings.to_file(os.path.join(gdata_root,'Berlin', 'Buildings_along_tram_route_M8.gpkg'), driver='GPKG')

In [ ]:
#drop unneseary tags & convert to 25833
buildings=buildings[['osmid','geometry']].to_crs(epsg=25833)
#Filter out point geometries
buildings=buildings.drop(buildings[buildings.geometry.geom_type=='Point'].index)

#optionally one can reduce the number of polygons by .dissolve().explode()

In [ ]:
tram_routes=tram_routes.to_crs(25833)

In [ ]:
tram_routes.geometry=tram_routes.line_merge()
tram_routes.geometry=tram_routes.geometry.segmentize(1)
#change the second route direction that it starts from Ahrensfelde/Stadtgrenze too
tram_routes.loc[1,'geometry']=tram_routes.geometry[1].reverse()

In [ ]:
#check if the direction is correct by picking some points from the beginning..
gpd.GeoDataFrame(geometry=[LineString(list(tram_routes.geometry[1].coords)[0:20])],crs=25833).explore()

In [ ]:
right_side = gpd.GeoDataFrame(geometry=[tram_routes.geometry[0].buffer(-400, single_sided=True)],crs=25833)
left_side = gpd.GeoDataFrame(geometry=[tram_routes.geometry[1].buffer(400, single_sided=True)],crs=25833)

buildings_right_side=buildings[buildings.intersects(right_side.geometry[0])]
buildings_left_side=buildings[buildings.intersects(left_side.geometry[0])]

#optional - merge touching polygons
#buildings_right_side = buildings_right_side.dissolve().explode().reset_index(drop=True)
#buildings_left_side = buildings_left_side.dissolve().explode().reset_index(drop=True)

#explode multiplolygons if any
buildings_right_side = buildings_right_side.explode().reset_index(drop=True)
buildings_left_side = buildings_left_side.explode().reset_index(drop=True)

In [ ]:
#I want to minimize projection distortions caused by tight curves of the track
#by projecting each building only to a reasonable small section of the track 

#with this one I calculate the distance from origin for each point of the line
def get_distance_indexes(line):
    all_points =  list(Point(xy) for xy in line.coords)
    points_gdf = gpd.GeoDataFrame(geometry=all_points, crs=25833)
    points_gdf['points_shifted']= points_gdf.geometry.shift(1)
    points_gdf['distance']=points_gdf.points_shifted.distance(points_gdf.geometry).fillna(0)
    points_gdf['distance']=points_gdf['distance'].cumsum()
    return points_gdf


line_A_H=get_distance_indexes(tram_routes.geometry[0])
line_H_A=get_distance_indexes(tram_routes.geometry[1])

#this function to get the section of the line
def get_segment_around_point(line,point,segment_length,df_indexes):
    all_points =  list(Point(xy) for xy in line.coords)
    
    center=line_locate_point(line,point)
    center_row_idx = (df_indexes['distance'] - center).abs().idxmin()
    
    if center_row_idx<len(all_points)-1:
        center_dist=LineString(all_points[0:center_row_idx+2]).length #we need at least two points for a line...
    else:
        center_dist=line.length
        
    min_dist_idx=(df_indexes['distance'] - (center_dist-segment_length/2)).abs().idxmin()
    max_dist_idx=(df_indexes['distance'] - (center_dist+segment_length/2)).abs().idxmin()               

    delta_x = LineString(df_indexes.geometry[0:min_dist_idx]).length
    return delta_x, LineString(df_indexes.geometry[min_dist_idx:max_dist_idx])

#Vertex-wise transformation: for each polygon vertex 
# calculate distance to the tram line -> y coordinate
# line_locate_point -> x coordinate w.r.t. the tram line

#calculate distance from line and disance from the beginning of the line vertex-wise
def project_polygon(polygon, line, df_indexes):
    polygon=polygon.segmentize(1) #needed to minimize distortion on curves around the route
    centrer = polygon.minimum_rotated_rectangle.centroid
    segment_length = polygon.minimum_rotated_rectangle.length
    
    delta_x, segment = get_segment_around_point(line,centrer,segment_length,df_indexes)
        
    gdf=gpd.GeoDataFrame(geometry=shortest_line([Point(x, y) for x, y in polygon.exterior.coords], segment),crs=25833)
    y=gdf.geometry.length.tolist()
    x=[line_locate_point(segment,Point(xy))+delta_x for xy in polygon.exterior.coords]
    return Polygon(list(zip(x, y)))

In [ ]:
#do the projection - takes quite some time
buildings_left_side_projected = buildings_left_side.geometry.apply(lambda x: project_polygon(x,tram_routes.geometry[1],line_A_H))

buildings_right_side_projected = buildings_right_side.geometry.apply(lambda x: project_polygon(x,tram_routes.geometry[0],line_H_A))
def invert_y_coordinates(polygon):
    inverted_coords = [(x, -y) for x, y in polygon.exterior.coords]
    return Polygon(inverted_coords)
buildings_right_side_projected = buildings_right_side_projected.apply(lambda x: invert_y_coordinates(x))

In [ ]:
buildings_right_side_projected=gpd.GeoDataFrame({'geometry': buildings_right_side_projected})
buildings_left_side_projected=gpd.GeoDataFrame({'geometry': buildings_left_side_projected})

In [ ]:
buildings_right_side_projected.to_file(os.path.join(gdata_root,'Berlin', 'tram_route_M8_buildings_right_projected.gpkg'), driver='GPKG')
buildings_left_side_projected.to_file(os.path.join(gdata_root,'Berlin', 'tram_route_M8_buildings_left_projected.gpkg'), driver='GPKG')

In [ ]:
#check the map
desired_width_px = 20000
desired_height_px = 800
dpi = 300

# Calculate the figure size in inches
fig_width_in = desired_width_px / dpi
fig_height_in = desired_height_px / dpi


fig, ax = plt.subplots(figsize=(fig_width_in, fig_height_in), dpi=dpi)
buildings_left_side_projected.plot(ax=ax, color='None', edgecolor='black',linewidth=0.5)
buildings_right_side_projected.plot(ax=ax, color='None', edgecolor='black',linewidth=0.1)

# Set equal scaling
ax.set_aspect('equal')
#ax.set_xlim(0, 20000)
#ax.set_ylim(-300, 300)
ax.axis('on')

In [ ]:
#adding tram stops information
stops=nodes_gdf[nodes_gdf.public_transport=='stop_position']
stops=stops.to_crs(25833).overlay(tram_routes[tram_routes.to=='S+U Hauptbahnhof'],how='intersection')
stops['distance']=line_locate_point(tram_routes.geometry[0],stops.geometry)
stops=stops[['name_1','geometry','distance']]
stops.geometry=list(Point(x,0) for x in stops['distance'])
stops =stops.sort_values('distance').reset_index(drop=True)
stops.head()

In [ ]:
#clean up a bit of space for labels
x_coords = [0, 400, 400, 0]
y_coords = [-250,-250, -900, -900]
polygon = Polygon(zip(x_coords, y_coords))
patch=gpd.GeoDataFrame(geometry=[polygon],crs=25833)
buildings_right_side_projected_patched=buildings_right_side_projected.overlay(patch,how='difference',keep_geom_type=False)

x_coords = [0, 1000, 1000, 0]
y_coords = [250,250, 900, 900]
polygon = Polygon(zip(x_coords, y_coords))
patch=gpd.GeoDataFrame(geometry=[polygon],crs=25833)
buildings_left_side_projected_patched=buildings_left_side_projected.overlay(patch,how='difference',keep_geom_type=False)

In [ ]:
#generate map
width_px = 20100
height_px = 850
dpi = 300
fig_width_in = width_px / dpi
fig_height_in = height_px / dpi


fig, ax = plt.subplots(figsize=(fig_width_in, fig_height_in), dpi=dpi)
buildings_left_side_projected_patched.plot(ax=ax, color='None', edgecolor='black',linewidth=0.5)
buildings_right_side_projected_patched.translate(yoff=-50).plot(ax=ax, color='None', edgecolor='black',linewidth=0.5)
stops.plot(ax=ax, marker='o', color='yellow', edgecolor='black', markersize=8, linewidth=0.5)

for i in range(1,len(stops)-2):
    ax.text(stops.geometry.x[i], stops.geometry.y[i] - 30, stops.name_1[i], ha='center', va='center', fontsize=4, color='black')
ax.text(stops.geometry.x[0], stops.geometry.y[0] - 30, stops.name_1[0], ha='left', va='center', fontsize=4, color='black')
ax.text(stops.geometry.x.iloc[-2], stops.geometry.y.iloc[-2] - 30, stops.name_1.iloc[-2], ha='right', va='center', fontsize=4, color='black')
ax.text(stops.geometry.x.iloc[-1], stops.geometry.y.iloc[-1] - 30, stops.name_1.iloc[-1], ha='right', va='center', fontsize=4, color='black')


text = "MetroTram-Linie M8, Berlin"
plt.text(0.002, 0.99, text, ha='left', va='top', transform=ax.transAxes, fontsize=10, color='black')
text = 'Ahrensfelde/Stadtgrenze<>S+U Hauptbahnhof'
plt.text(0.002, 0.92, text, ha='left', va='top', transform=ax.transAxes, fontsize=6, color='black')
text = "github.com/Ossssip\nMap data from OpenStreetMap"
plt.text(0.002, 0.01, text, ha='left', va='bottom', transform=ax.transAxes, fontsize=4, color='black')


ax.set_aspect('equal')
ax.set_xlim(-10, 19950)
ax.set_ylim(-450, 400)
ax.axis('off')
plt.savefig(os.path.join(gdata_root,'Berlin', 'tram_route_M8_strip_map.png'), bbox_inches='tight', dpi=600, pad_inches=0.1, facecolor="white")


In [ ]:
#First, I parepare bw and color versions of the map without labels
width_px = 23000
height_px = 1200
dpi = 300
fig_width_in = width_px / dpi
fig_height_in = height_px / dpi
fig, ax = plt.subplots(figsize=(fig_width_in, fig_height_in), dpi=dpi)


cmap = plt.get_cmap('viridis')
norm = plt.Normalize(vmin=0, vmax=400)

def get_gradient_lines(geom, cmap, norm):
    segments = []
    colors = []
    if geom.geom_type == 'Polygon':
        exterior = geom.exterior
        x, y = exterior.xy
        y_abs = np.abs(y)
        for i in range(len(x) - 1):
            segments.append([[x[i], y[i]], [x[i+1], y[i+1]]])
            colors.append(y_abs[i])
    elif geom.geom_type == 'MultiPolygon': #not really needed anymore...
        for poly in geom:
            exterior = poly.exterior
            x, y = exterior.xy
            y_abs = np.abs(y)
            for i in range(len(x) - 1):
                segments.append([[x[i], y[i]], [x[i+1], y[i+1]]])
                colors.append(y_abs[i])
    segments = np.array(segments)
    colors = np.array(colors)
    return segments, colors

stops.plot(ax=ax, marker='o', color='yellow', edgecolor='black', markersize=8, linewidth=0.5)
for i in range(1,len(stops)-2):
    ax.text(stops.geometry.x[i], stops.geometry.y[i] - 30, stops.name_1[i], ha='center', va='center', fontsize=6, color='black')
ax.text(stops.geometry.x[0], stops.geometry.y[0] - 30, stops.name_1[0], ha='left', va='center', fontsize=6, color='black')
ax.text(stops.geometry.x.iloc[-2], stops.geometry.y.iloc[-2] - 30, stops.name_1.iloc[-2], ha='right', va='center', fontsize=6, color='black')
ax.text(stops.geometry.x.iloc[-1], stops.geometry.y.iloc[-1] - 30, stops.name_1.iloc[-1], ha='right', va='center', fontsize=6, color='black')


for geom in buildings_left_side_projected.geometry:
    segments, colors = get_gradient_lines(geom, cmap, norm)
    lc = LineCollection(segments, cmap=cmap, norm=norm, linewidth=0.5)
    lc.set_array(colors)
    ax.add_collection(lc)
for geom in buildings_right_side_projected.translate(yoff=-50).geometry:
    segments, colors = get_gradient_lines(geom, cmap, norm)
    lc = LineCollection(segments, cmap=cmap, norm=norm, linewidth=0.5)
    lc.set_array(colors)
    ax.add_collection(lc)

ax.set_aspect('equal')
ax.set_xlim(-1550, 21450)
ax.set_ylim(-600, 600)
ax.axis('off')
#getting no margins is hard...
plt.tight_layout(pad=0)
plt.margins(0,0)
plt.close()
fig.canvas.draw()
image_col = np.frombuffer(fig.canvas.buffer_rgba(), dtype=np.uint8).reshape(fig.canvas.get_width_height()[::-1] + (4,))



fig, ax = plt.subplots(figsize=(fig_width_in, fig_height_in), dpi=dpi)
buildings_left_side_projected.plot(ax=ax, color='None', edgecolor='black',linewidth=0.5)
buildings_right_side_projected.translate(yoff=-50).plot(ax=ax, color='None', edgecolor='black',linewidth=0.5)
stops.plot(ax=ax, marker='o', color='yellow', edgecolor='black', markersize=8, linewidth=0.5)

for i in range(1,len(stops)-2):
    ax.text(stops.geometry.x[i], stops.geometry.y[i] - 30, stops.name_1[i], ha='center', va='center', fontsize=6, color='black')
ax.text(stops.geometry.x[0], stops.geometry.y[0] - 30, stops.name_1[0], ha='left', va='center', fontsize=6, color='black')
ax.text(stops.geometry.x.iloc[-2], stops.geometry.y.iloc[-2] - 30, stops.name_1.iloc[-2], ha='right', va='center', fontsize=6, color='black')
ax.text(stops.geometry.x.iloc[-1], stops.geometry.y.iloc[-1] - 30, stops.name_1.iloc[-1], ha='right', va='center', fontsize=6, color='black')

ax.set_aspect('equal')
ax.set_xlim(-1550, 21450)
ax.set_ylim(-600, 600)
ax.axis('off')
plt.tight_layout(pad=0)
plt.margins(0,0)
plt.show()
fig.canvas.draw()
image_bw = np.frombuffer(fig.canvas.buffer_rgba(), dtype=np.uint8).reshape(fig.canvas.get_width_height()[::-1] + (4,))

In [ ]:
# code to mimic zoom lens distortion...
# see https://stackoverflow.com/a/76335623

class BarrelDeformer:
    def __init__(self, w, h, k_1=1, k_2=0.05, zoom_factor=0.55):
        self.w = w
        self.h = h
        self.k_1 = k_1
        self.k_2 = k_2
        self.zoom_factor = zoom_factor

    def transform(self, x, y):
        # center and scale the grid for radius calculation (distance from center of image)
        x_c, y_c = self.w / 2, self.h / 2 
        x = (x - x_c) / x_c
        y = (y - y_c) / y_c
        radius = np.sqrt(x**2 + y**2) # distance from the center of image
        m_r = 1 + self.k_1 * radius + self.k_2 * radius**2 # radial distortion model
        # apply the model 
        x, y = x * m_r * self.zoom_factor, y * m_r * self.zoom_factor
        # reset all the shifting
        x, y = x * x_c + x_c, y * y_c + y_c
        return x, y

    def transform_rectangle(self, x0, y0, x1, y1):
        return (*self.transform(x0, y0),
                *self.transform(x0, y1),
                *self.transform(x1, y1),
                *self.transform(x1, y0),
                )

    def getmesh(self, img):
        self.w, self.h = img.size
        gridspace = 20
        target_grid = []
        for x in range(0, self.w, gridspace):
            for y in range(0, self.h, gridspace):
                target_grid.append((x, y, x + gridspace, y + gridspace))
        source_grid = [self.transform_rectangle(*rect) for rect in target_grid]
        return [t for t in zip(target_grid, source_grid)]

In [ ]:
width_px = 1600
height_px = 1200
dpi = 300
fig_width_in = width_px / dpi
fig_height_in = height_px / dpi

def get_distorted_image(image_col,image_bw):
    w, h = image_col.size
    #I had to play a bit with the barrel distortion
    im_deformed = ImageOps.deform(image_col, BarrelDeformer(w, h, k_1=.8, k_2=1.6, zoom_factor=0.40))
    #im_deformed = ImageOps.deform(image_col, BarrelDeformer(w, h, k_1=.8, k_2=1.6, zoom_factor=0.38))
    #im_deformed = ImageOps.deform(image_color, BarrelDeformer(w, h, k_1=.9, k_2=-2.0, zoom_factor=.95))
    
    #Create a circular mask
    mask = Image.new("L", (w, h), 0)
    draw = ImageDraw.Draw(mask)
    lens_radius = 530 
    lens_center = (w // 2, h // 2)  # Center of the lens
    draw.ellipse((lens_center[0] - lens_radius, lens_center[1] - lens_radius, 
                  lens_center[0] + lens_radius, lens_center[1] + lens_radius), fill=255)
    # Extract the lens area from the distorted image
    distorted_lens_area = Image.composite(im_deformed, Image.new("RGBA", (w, h)), mask)
    # Composite the lens area on top of the original image
    final_image = Image.composite(distorted_lens_area, image_bw, mask)
    
    fig, ax = plt.subplots(figsize=(fig_width_in, fig_height_in), dpi=dpi)
    ax.imshow(final_image)
    ax.axis('off')
    #a circle to represent the lens
    circle = Circle(lens_center, lens_radius, fill=False, edgecolor='gray', linewidth=1.25)
    #add labels
    ax.add_patch(circle)
    text = "MetroTram-Linie M8, Berlin"
    ax.text(0.02, 0.98, text, ha='left', va='top', transform=ax.transAxes, fontsize=8, color='black')
    text = 'Ahrensfelde/Stadtgrenze<>S+U Hauptbahnhof'
    ax.text(0.98, 0.98, text, ha='right', va='top', transform=ax.transAxes, fontsize=6, color='black')
    text = "github.com/Ossssip\nMap data from OpenStreetMap"
    ax.text(0.98, 0.02, text, ha='right', va='bottom', transform=ax.transAxes, fontsize=6, color='black')
    plt.tight_layout(pad=0)
    plt.close()
    fig.canvas.draw()
    image = np.frombuffer(fig.canvas.buffer_rgba(), dtype=np.uint8).reshape(fig.canvas.get_width_height()[::-1] + (4,))
    image_masked = Image.fromarray(image)
    return image_masked



height, width, _ = image_bw.shape


for i, x in enumerate(range(0, width-width_px+1, 10)):
    img_cut_bw = image_bw[:, x:x + width_px, :]
    img_cut_col = image_col[:, x:x + width_px, :]
    
    img_cut_bw_pil = Image.fromarray(img_cut_bw)
    img_cut_col_pil = Image.fromarray(img_cut_col)

    image_masked = get_distorted_image(img_cut_col_pil, img_cut_bw_pil)
    png_filename = os.path.join(gdata_root,'Berlin', 'img', f'image_{i:05d}.png')
    image_masked.save(png_filename)

#and then convert to video with ffmpeg -framerate 30 -pattern_type sequence -i 'image_%05d.png'  -c:v libx264 -pix_fmt yuv420p -crf 35 -preset slow movie.mp4